# Math 124 - Programming for Mathematical Applications
Per-Olof Persson, UC Berkeley

## Homework 9

In [ ]:
using LinearAlgebra, Plots   # Packages needed

# For fast Jupyter plotting
function fastdisplay(h=current())
    fname = savefig(h, tempname())
    display("image/png", read(fname))
    rm(fname, force=true)
end

### Problem 1: Building a Cubic Spline

We're going to interpolate $n+1$ data points $(x_i,y_i)$, for $i=0,\ldots,n$. A *cubic spline function* $S(x)$ is a special function that connects these points smoothly. It's 'piecewise' because it's defined by a different cubic polynomial $S_j(x)$ on each interval $[x_j, x_{j+1}]$.

For $x$ in the interval $[x_j, x_{j+1}]$, the polynomial is:

$$
S_j(x) = y_j + b_j(x-x_j)+c_j(x-x_j)^2+d_j(x-x_j)^3
$$

Our goal is to find the coefficients $b_j, c_j, d_j$ for each piece (for $j=0,\ldots,n-1$). These coefficients are calculated to ensure the entire spline $S(x)$ not only hits every data point (interpolates) but also has a smooth transition at each point (continuous first and second derivatives).

To keep all the parts of our spline organized (the data points and the coefficients), we'll define a custom `struct` in Julia.

In [ ]:
struct Spline
    x::Vector # (n+1) x-coordinates of the data points (knots)
    y::Vector # (n+1) y-coordinates of the data points (knots)
    b::Vector # (n) linear coefficients
    c::Vector # (n+1) quadratic coefficients (from solving the system)
    d::Vector # (n) cubic coefficients
end

It's helpful to have a nice way to print our `Spline` object. We can *overload* the `Base.show` function, which is what Julia uses to display objects in the terminal or notebook.

In [ ]:
function Base.show(io::IO, S::Spline)
    # This custom 'show' method prints a descriptive summary of our Spline object
    n = length(S.x) - 1
    print(io, "CubicSpline with $(n+1) data points (n=$n intervals)")
end

#### Problem 1(a): The `Spline` Constructor

Write a *constructor* function that acts like a factory for our `Spline` objects. It should have the syntax `S = Spline(x, y)`.

This function will take the data points `x` and `y` as input, perform the necessary calculations to find the coefficient vectors `b`, `c`, and `d`, and then return a new `Spline` object containing all this information.

Here's the plan:
1.  Calculate the $n$ interval lengths $h_j=x_{j+1}-x_j$ for $j=0,\ldots,n-1$.
2.  Set up the tridiagonal linear system $A\boldsymbol{c}=\boldsymbol{f}$ for the $\boldsymbol{c}$ coefficients. Use Julia's `Tridiagonal(dl, d, du)` type for efficiency. $A$ is an $(n+1) \times (n+1)$ matrix.

$$
\begin{align*}
A &=
\begin{pmatrix}
1 & 0 \\
h_0 & 2(h_0+h_1) & h_1 \\
    & \ddots & \ddots & \ddots \\
    &  & h_{n-2} & 2(h_{n-2}+h_{n-1}) & h_{n-1} \\
    &  &         & 0 & 1
\end{pmatrix} \\
\boldsymbol{f}&=(0,3(y_2-y_1)/h_1-3(y_1-y_0)/h_0,\ldots, \\
      &\ \ \ \ \ \ \ \ \ 3(y_n-y_{n-1})/h_{n-1}-3(y_{n-1}-y_{n-2})/h_{n-2},0)^T \\
\boldsymbol{c}&=(c_0,\ldots,c_n)^T
\end{align*}
$$

   (Note: The `1`s on the diagonal of $A$ and `0`s in $\boldsymbol{f}$ correspond to the *natural spline* condition, which sets the second derivative to zero at the endpoints, $S''(x_0) = S''(x_n) = 0$. This implies $c_0=0$ and $c_n=0$.)

3.  Solve $A\boldsymbol{c}=\boldsymbol{f}$ to find the vector $\boldsymbol{c}$ (which has $n+1$ elements).
4.  Compute the $\boldsymbol{b}$ and $\boldsymbol{d}$ vectors (each with $n$ elements) using the formulas for $j=0,\ldots,n-1$:

$$
\begin{align*}
b_j &= (y_{j+1}-y_j)/h_j-h_j(2c_j+c_{j+1})/3 \\
d_j &= (c_{j+1}-c_j)/(3h_j)
\end{align*}
$$

5.  Return a `Spline` object populated with `x`, `y`, `b`, `c`, and `d`.

#### Problem 1(b): Making the Spline Callable

Let's make our `Spline` object behave like a function. We can do this by *overloading the call operator* `()`.

Implement the function `(S::Spline)(xx)`.
1.  It should take a `Spline` object `S` and a single $x$-coordinate `xx` as input.
2.  It needs to first find the correct interval $[x_j, x_{j+1}]$ that contains `xx`.
3.  Once it finds the interval $j$, it should evaluate the $j$-th polynomial $S_j(xx)$ using the formula:
    $$S_j(xx) = y_j + b_j(xx-x_j)+c_j(xx-x_j)^2+d_j(xx-x_j)^3$$
4.  If `xx` is *outside* the entire domain $[x_0, x_n]$, the function should return `0.0`.

#### Problem 1(c): Test the Spline

Time to see our spline in action. We'll test it by interpolating a known function:

$$
f(x) = e^{-x/2}\sin 2x
$$

1.  Create your $n+1 = 11$ data points by sampling $f(x)$ at the integers $x_i = i$ for $i=0,\ldots,10$.
2.  Create a `Spline` object `S` using these `x` and `y` data points.
3.  Generate a fine-grained set of $x$-values (e.g., `xx = 0:0.01:10`) to plot a smooth curve.
4.  Evaluate both the original function `f.(xx)` and your spline `S.(xx)` at these points. (Note the `.` for broadcasting the function call to every element in `xx`!)
5.  Create a plot that shows:
    * The original function `f(x)` as a line.
    * The spline interpolant `S(x)` as another line.
    * The original data points $(x_i, y_i)$ as markers (e.g., using `scatter!`).

### Problem 2: Parametric Spline Curves

Now let's use own splines to represent curves in the $x,y$-plane. Instead of $y$ being a function of $x$ ($y=f(x)$), what if we want to draw a curve that can loop back on itself, like a signature or a shape? 

We can use a *parametric spline curve*. The idea is to treat the $x$ and $y$ coordinates as two *separate* functions of a new parameter, $t$. 

$$ \boldsymbol{p}(t) = (x(t), y(t)) $$

Given $n+1$ data points $(x_i, y_i)$ for $i=0,\ldots,n$, we can create two standard cubic splines using our `Spline` constructor:
1.  One spline, $S_x(t)$, that interpolates the points $(t_i, x_i)$.
2.  A second spline, $S_y(t)$, that interpolates the points $(t_i, y_i)$.

For simplicity, we'll just use the index $i$ as the parameter value, so $t_i = i$. By evaluating $(S_x(t), S_y(t))$ for values of $t$ from $0$ to $n$, we trace out a smooth curve that passes through all our data points in order.

#### Problem 2(a): Plotting a Parametric Curve

Write a function `plot_parametric_spline(x, y; r=10)` that calculates and plots a single parametric spline curve.

1.  Input: The `x` and `y` vectors of the data points.
2.  Parameter: `r` controls the smoothness of the plot. We'll evaluate the spline at `r` points *per interval*.
3.  Inside the function:
    - a.  Determine $n$ (`length(x) - 1`).
    - b.  Create the parameter vector `t = 0:n`.
    - c.  Create the $x$-spline: `Sx = Spline(t, x)`.
    - d.  Create the $y$-spline: `Sy = Spline(t, y)`.
    - e.  Create a fine-grained $t$-vector for plotting: `tt = 0:1/r:n`. (This evaluates at `r` points per unit interval).
    - f.  Evaluate `Sx.(tt)` and `Sy.(tt)` to get the plotted coordinates.
    - g.  Use `plot!(...)` to add the curve to the *current* plot. This allows us to draw multiple curves on the same axes.

Let's test our `plot_parametric_spline` function with a simple shape.

In [ ]:
# Define the 6 data points for our test shape
x = [0, 1, 1, 2, 2, 1]
y = [0, 0, 1, 1, 0, -1]

# Create a new plot, setting aspect ratio to :equal
# This ensures 1 unit on the x-axis is the same length as 1 unit on the y-axis
plot(legend=false, aspect_ratio=:equal, title="Test Parametric Spline")

# Add our spline curve to the plot
plot_parametric_spline(x, y)

# Add markers for the original data points
scatter!(x, y, label="Data Points")

#### Problem 2(b): Reading Spline Data from a File

Now for a more complex example. We have a file, [`bmw.dat` (downloadable)](https://raw.githubusercontent.com/popersson/math124files/main/homework/bmw.dat), that contains the data for many different spline curves to draw a car.

The file has a specific format:
1.  A line with a single integer, $N_k$, (the number of points in the *k*-th spline).
2.  $N_k$ lines, each with an $x$ $y$ coordinate pair, separated by a space.
3.  This pattern repeats for the next spline curve, until the end of the file.

Your task is to write a function `read_splines(fname)` that reads this file.

* It should loop until it reaches the `eof(fid)` (end of file).
* Inside the loop, it should: 
    1.  Read a line and `parse` it to an `Int64` to get $N_k$.
    2.  Create a `zeros(2, N_k)` matrix to hold the points.
    3.  Loop $N_k$ times: 
        a.  Read the next line.
        b.  `split` the line by spaces and `parse` the parts into `Float64`s.
        c.  Store this `[x, y]` vector in the $i$-th column of your matrix.
    4.  `push!` this $2 \times N_k$ matrix into a holding array (e.g., `xy_coords`).
* The function should return the `xy_coords` array. This will be an array of matrices (`Vector{Matrix{Float64}}`).

Let's test the `read_splines` function. (This assumes you've downloaded `bmw.dat` and it's in the same directory as this notebook!)

In [ ]:
xy_coords = read_splines("bmw.dat")

# We can check the type, it should be something like Vector{Matrix{Float64}}
println("Type of xy_coords: ", typeof(xy_coords))
# Let's also see how many separate spline curves we loaded
println("Number of splines loaded: ", length(xy_coords))

#### Problem 2(c): Plotting the Full Geometry

Now we'll write a function to plot *all* the splines we just read.

Write `plot_parametric_splines(xy_coords)`:
1.  It should take the `xy_coords` array (of matrices) as input.
2.  It should loop through each matrix `xy` in `xy_coords`.
3.  For each `xy` matrix, it should call our `plot_parametric_spline` function from 2(a). Remember to pass the x-coordinates (`xy[1,:]`) and y-coordinates (`xy[2,:]`) separately.

Finally, let's draw the car! We'll plot it twice: once to see the whole thing, and a second time zoomed in on the details.

In [ ]:
plot(legend=false, aspect_ratio=:equal, title="BMW Spline Geometry")
plot_parametric_splines(xy_coords)
fastdisplay() # Use our helper for fast display

In [ ]:
plot(legend=false, aspect_ratio=:equal,
     title="Zoomed-in View",
     xlims=(-121,-110), ylims=(10,19))
plot_parametric_splines(xy_coords)
fastdisplay()

#### Problem 2(d): Designing New Types

*(No submission required, but this is a key concept in good software design)*

Think about our solution for Problem 2. We have two separate `Spline` objects, `Sx` and `Sy`, that are logically linked. Every time we want to evaluate or plot the parametric curve, we have to manage both of them together.

This is a good sign that we could benefit from creating a new custom type!

* **Question 1:** Would it make sense to define a new composite type `ParametricSpline`?

* **Question 2:** If you did, what fields (member variables) would you include in its `struct` definition?

* **Question 3:** What functions or operators would you overload for this new type to make it easy to use? (e.g., how would you *evaluate* it at a parameter $t$? How would you *plot* it?)